In [ ]:
from huggingface_hub import HfApi
from huggingface_hub import HfApi
api = HfApi()
# 替换为你的用户名/仓库名
repo_id = "vincentchao/qllava-next"
# # 创建仓库(如果还不存在)
api.create_repo(repo_id, repo_type="model", private=False)

# 上传整个目录
api.upload_folder(
    folder_path="/common/home/users/w/wzhao/vqclip/qllava_next_newest",
    repo_id=repo_id,
    repo_type="model"
)

In [1]:
classes2id = { 'neutral':0, 'porn':1,'gun':2,'cigarette':3,'alcohol':4, 'knife':5,'blood':6,'insulting_gesture':7}
id2class = ['neutral','porn','gun','cigarette','alcohol',"knife",'blood','insulting_gesture']

In [2]:
from transformers import LlavaProcessor
import torch
import logging
from transformers import TrainerCallback

import datetime
import os
#os.environ["CUDA_VISIBLE_DEVICES"] = "0"  # 只显示第一个GPU设备
import torch  # 或 tensorflow 等
import torch.nn as nn
import os
import torch.distributed as dist
from transformers import LlavaProcessor
from qllava3_test import LlavaNextForConditionalGeneration
# %%
model_id = "/common/public/llava/llama3-llava-next-8b-hf"
processor = LlavaProcessor.from_pretrained(
    model_id ,
)

# 加载模型
model = LlavaNextForConditionalGeneration.from_pretrained(
    "/common/home/users/w/wzhao/vqclip/qllava_next_newest", 
    #"/common/home/users/w/wzhao/qllava/vqllava/checkpoint-260",
    # "/common/home/users/w/wzhao/"+path + "/checkpoint-5000",
    torch_dtype=torch.float32,  # 仍然使用float16以节省内存
).cuda()

Loading checkpoint shards:   0%|          | 0/7 [00:00<?, ?it/s]

In [ ]:
from PIL import Image
import torch
import os
import json
import re

# 假设 processor 和 model 已经初始化好了
# 如果没有，需要添加相关的初始化代码

def get_category_from_path(path):
    """从路径中提取类别"""
    if "porn" in path:
        return "porn"
    elif "blood" in path:
        return "blood"
    elif "gun" in path:
        return "gun"
    elif "insulting_gesture" in path:
        return "insulting_gesture"
    elif "alcohol" in path:
        return "alcohol"
    elif "cigarette" in path:
        return "cigarette"
    elif "knife" in path:
        return "knife"
    elif "real_neutral" in path:
        return "neutral"
    else:
        return "unknown"

def process_image(image_path, processor, model):
    """处理图像并获取描述"""
    try:
        image = Image.open(image_path)
        
        conversation = [
            {
              "role": "user",
              "content": [
                  {"type": "text", "text": "Describe this image "},
                  {"type": "image"},
                ],
            }, 
        ]
        
        prompt = processor.apply_chat_template(conversation, add_generation_prompt=True)
        
        inputs = processor(images=image, text=prompt, return_tensors="pt").to(model.device)
        
        with torch.no_grad():
            output = model.generate(**inputs, max_new_tokens=10)  # 增加 token 数量以获取更详细的描述
        
        description = processor.decode(output[0], skip_special_tokens=True)
        
        # 清理描述文本，移除提示和可能的系统消息
        # 这部分可能需要根据实际输出进行调整
        description = re.sub(r"Describe this image\s*", "", description)
        
        return description
    except ValueError as e:
        error_data = e.args[0]  # 这将获取到 [indices, categories[0]]
        
        # 提取 indices 和 categories[0]
        if isinstance(error_data, list) and len(error_data) == 2:
            captured_indices = error_data[0]
            captured_category = error_data[1]

        return f"Error processing image: {id2class[captured_category]} index {captured_indices}"

def main():
    image_folders = [
        "/common/home/users/w/wzhao/llava_helper/nsfw_dataset_v1/porn/train",
        "/common/home/users/w/wzhao/llava_helper/nsfw_dataset_v1/porn/test",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/blood/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/blood/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/gun/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/gun/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/insulting_gesture/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/insulting_gesture/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/alcohol/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/alcohol/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/cigarette/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/cigarette/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/knife/testing/jpg",
        "/common/home/users/w/wzhao/llava_helper/dataset/class/knife/training/jpg",
        "/common/home/users/w/wzhao/llava_helper/real_neutral"
    ]
    
    results = []
    total_images = 0
    
    # 计算总图片数量
    for folder in image_folders:
        if os.path.exists(folder):
            for root, _, files in os.walk(folder):
                total_images += sum(1 for f in files if f.lower().endswith(('.png', '.jpg', '.jpeg')))
    
    print(f"Total images to process: {total_images}")
    
    processed_count = 0
    
    # 处理每个文件夹中的图片
    for folder in image_folders:
        if not os.path.exists(folder):
            print(f"Folder not found: {folder}")
            continue
            
        category = get_category_from_path(folder)
        print(f"Processing folder: {folder} (Category: {category})")
        
        for root, _, files in os.walk(folder):
            for file in files:
                if file.lower().endswith(('.png', '.jpg', '.jpeg')):
                    image_path = os.path.join(root, file)
                    
                    # 处理图像
                    description = process_image(image_path, processor, model)
                    
                    # 存储结果
                    results.append({
                        "path": image_path,
                        "response": description,
                        "category": category
                    })
                    
                    processed_count += 1
                    if processed_count % 10 == 0:
                        print(f"Processed {processed_count}/{total_images} images")
                    
                    # 每处理100张图片保存一次中间结果
                    if processed_count % 100 == 0:
                        with open(f"/common/home/users/w/wzhao/vqclip/json_results_newest/image_descriptions_checkpoint_{processed_count}.json", "w") as f:
                            json.dump(results, f, indent=2)
    
    # 保存最终结果
    with open("/common/home/users/w/wzhao/vqclip/json_results_newest/image_descriptions_complete.json", "w") as f:
        json.dump(results, f, indent=2)
    
    print(f"Processing complete. Results saved to image_descriptions_complete.json")

if __name__ == "__main__":
    # 确保已经初始化了processor和model
    # 如果没有，需要在这里添加初始化代码
    main()

Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


Total images to process: 21213
Processing folder: /common/home/users/w/wzhao/llava_helper/nsfw_dataset_v1/porn/train (Category: porn)
this is q_latent_loss tensor(8.8170, device='cuda:0')
This is e_latent_loss tensor(2.2042, device='cuda:0')
57
[0]


Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


this is q_latent_loss tensor(11.6122, device='cuda:0')
This is e_latent_loss tensor(2.9030, device='cuda:0')
57
[0]
this is q_latent_loss tensor(9.9424, device='cuda:0')
This is e_latent_loss tensor(2.4856, device='cuda:0')
57
[0]
this is q_latent_loss tensor(11.4321, device='cuda:0')
This is e_latent_loss tensor(2.8580, device='cuda:0')
57
[0]


Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


...

Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


this is q_latent_loss tensor(7.8044, device='cuda:0')
This is e_latent_loss tensor(1.9511, device='cuda:0')
57
[0]
this is q_latent_loss tensor(8.0274, device='cuda:0')
This is e_latent_loss tensor(2.0068, device='cuda:0')
57
[0]
this is q_latent_loss tensor(8.4584, device='cuda:0')
This is e_latent_loss tensor(2.1146, device='cuda:0')
57
[0]


Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


this is q_latent_loss tensor(8.1515, device='cuda:0')
This is e_latent_loss tensor(2.0379, device='cuda:0')
57
[0]
this is q_latent_loss tensor(9.8069, device='cuda:0')
This is e_latent_loss tensor(2.4517, device='cuda:0')
57
[0]
this is q_latent_loss tensor(10.3290, device='cuda:0')
This is e_latent_loss tensor(2.5823, device='cuda:0')
57
[0]


Setting `pad_token_id` to `eos_token_id`:None for open-end generation.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


In [ ]:
import numpy as np
np.load("/common/home/users/w/wzhao/vqclip/classified_results/1.npy")

array(['54', 'porn'], dtype='<U21')

In [ ]:
from PIL import Image
import time
image = Image.open('/common/home/users/w/wzhao/qllava/00008.jpg')
#image = Image.open('/common/home/users/w/wzhao/qllava/94915.jpg')
#image = Image.open("")
# Define a chat histiry and use `apply_chat_template` to get correctly formatted prompt
# Each value in "content" has to be a list of dicts with types ("text", "image") 
print("**************************************************************")


conversation = [
    {
      "role": "user",
      "content": [
          {"type": "text", "text": "Describe this image "},
          {"type": "image"},
        ],
    }, 
]

prompt = processor.apply_chat_template(conversation, add_generation_prompt=True)
#print(prompt)

inputs = processor(images=image, text=prompt, return_tensors="pt").to(model.device)
print(inputs["pixel_values"].shape)

# autoregressively complete prompt
try:
    output = model.generate(**inputs, max_new_tokens=50)
    print(processor.decode(output[0], skip_special_tokens=True))
except ValueError as e:
    # 记录错误信息
    
    harm_class = int(str(e)))

    
    # 可以选择继续执行其他代码或者返回一个预设的安全输出
    print("检测到不适当内容，生成已停止")
print("**************************************************************")
#time.sleep(100)

**************************************************************
torch.Size([1, 3, 336, 336])
this is q_latent_loss tensor(0.6994, device='cuda:0')
This is e_latent_loss tensor(0.1748, device='cuda:0')
34
[1]
1
检测到不适当内容，生成已停止
**************************************************************


In [ ]:
model

LlavaForConditionalGeneration(
  (vision_tower): CLIPVisionModel(
    (vision_model): CLIPVisionTransformer(
      (embeddings): CLIPVisionEmbeddings(
        (patch_embedding): Conv2d(3, 1024, kernel_size=(14, 14), stride=(14, 14), bias=False)
        (position_embedding): Embedding(577, 1024)
      )
      (pre_layrnorm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
      (encoder): CLIPEncoder(
        (layers): ModuleList(
          (0-23): 24 x CLIPEncoderLayer(
            (self_attn): CLIPSdpaAttention(
              (k_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (v_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (q_proj): Linear(in_features=1024, out_features=1024, bias=True)
              (out_proj): Linear(in_features=1024, out_features=1024, bias=True)
            )
            (layer_norm1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
            (mlp): CLIPMLP(
              (activation_fn): Q

In [ ]:
model.save_pretrained(
    "/common/home/users/w/wzhao/vqclip/VQLLMfinal"
)

[2025-03-28 01:00:17,048] [WARNING] [real_accelerator.py:174:get_accelerator] Setting accelerator to CPU. If you have GPU or other accelerator, we were unable to detect it.
[2025-03-28 01:00:17,049] [INFO] [real_accelerator.py:219:get_accelerator] Setting ds_accelerator to cpu (auto detect)


/opt/apps/software/Anaconda3/2024.06-1/compiler_compat/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


AttributeError: 'list' object has no attribute 'device'

In [ ]:
print(type(model))

<class 'qllava_new.LlavaForConditionalGeneration'>


In [2]:
import numpy as np
np.load("/common/home/users/w/wzhao/vqclip/classified_results_llama2/1.npy")

array([56,  1])

In [6]:
import os
import numpy as np
import json
from collections import defaultdict
import pickle

# 定义目录路径
directory_path = '/common/home/users/w/wzhao/vqclip/classified_results_llama2'

# 创建一个嵌套字典，用于存储每个类别中每个元素ID出现的次数
class_element_counts = defaultdict(lambda: defaultdict(int))
# 创建一个字典用于存储每个类别的总计数
class_total_counts = defaultdict(int)

# 遍历目录中的所有.npy文件
try:
    for filename in os.listdir(directory_path):
        if filename.endswith('.npy'):
            file_path = os.path.join(directory_path, filename)
            
            # 加载.npy文件
            data = np.load(file_path)
            
            # 确保数据格式正确
            if data.size == 2:
                element_id = int(data[0])  # 确保是整数
                class_id = int(data[1])    # 确保是整数
                
                # 增加该元素在对应类别中的计数
                class_element_counts[class_id][element_id] += 1
                # 增加该类别的总计数
                class_total_counts[class_id] += 1
            else:
                print(f"警告: 文件 {filename} 的数据格式不符合预期，已跳过")
    
    # 将defaultdict转换为普通dict以便序列化
    result_dict = {
        "class_totals": dict(class_total_counts),
        "class_elements": {
            class_id: dict(elements) 
            for class_id, elements in class_element_counts.items()
        }
    }
    
    # 保存结果到JSON文件
    output_json_path = os.path.join(os.path.dirname(directory_path), "classification_stats.json")
    with open(output_json_path, 'w') as f:
        json.dump(result_dict, f, indent=2)
    
    # 也保存为Python pickle格式，这样在后续Python处理中更方便
    output_pickle_path = os.path.join(os.path.dirname(directory_path), "classification_stats.pkl")
    with open(output_pickle_path, 'wb') as f:
        pickle.dump(result_dict, f)
    
    # 打印一些基本统计信息
    print(f"统计结果已保存到字典并导出到：")
    print(f"- JSON: {output_json_path}")
    print(f"- Pickle: {output_pickle_path}")
    print("\n基本统计信息:")
    print(f"总共发现 {len(class_total_counts)} 个不同的类别")
    total_elements = sum(class_total_counts.values())
    print(f"总共处理了 {total_elements} 个元素")
    
    # 打印每个类别的样本统计
    print("\n各类别的统计摘要:")
    for class_id in sorted(class_total_counts.keys()):
        print(f"类别 {class_id}: 包含 {class_total_counts[class_id]} 个元素，有 {len(class_element_counts[class_id])} 个不同的元素ID")
        
        # 获取该类别中出现次数最多的3个元素
        sorted_elements = sorted(class_element_counts[class_id].items(), 
                                key=lambda x: x[1], reverse=True)[:3]
        
        # 打印这些元素及其出现次数
        print(f"  出现频率最高的元素: " + ", ".join([f"ID {e_id}: {count}次" for e_id, count in sorted_elements]))

except Exception as e:
    print(f"发生错误: {e}")

统计结果已保存到字典并导出到：
- JSON: /common/home/users/w/wzhao/vqclip/classification_stats.json
- Pickle: /common/home/users/w/wzhao/vqclip/classification_stats.pkl

基本统计信息:
总共发现 8 个不同的类别
总共处理了 21213 个元素

各类别的统计摘要:
类别 0: 包含 5413 个元素，有 43 个不同的元素ID
  出现频率最高的元素: ID 16: 615次, ID 60: 609次, ID 14: 566次
类别 1: 包含 5554 个元素，有 4 个不同的元素ID
  出现频率最高的元素: ID 56: 2067次, ID 7: 1430次, ID 34: 1180次
类别 2: 包含 1473 个元素，有 3 个不同的元素ID
  出现频率最高的元素: ID 13: 778次, ID 24: 488次, ID 23: 207次
类别 3: 包含 2134 个元素，有 4 个不同的元素ID
  出现频率最高的元素: ID 46: 840次, ID 33: 641次, ID 39: 351次
类别 4: 包含 1416 个元素，有 2 个不同的元素ID
  出现频率最高的元素: ID 22: 748次, ID 42: 668次
类别 5: 包含 2785 个元素，有 2 个不同的元素ID
  出现频率最高的元素: ID 52: 1654次, ID 4: 1131次
类别 6: 包含 1723 个元素，有 5 个不同的元素ID
  出现频率最高的元素: ID 20: 555次, ID 57: 481次, ID 17: 350次
类别 7: 包含 715 个元素，有 1 个不同的元素ID
  出现频率最高的元素: ID 40: 715次
